In [ ]:
import networkx as nx
import osmnx as ox
import pandas as pd
import geopandas as gpd
import folium
import numpy as np

%matplotlib inline
ox.__version__

useful_tags_path = ['bridge', 'tunnel', 'oneway', 'lanes', 'ref', 'name',
                    'highway', 'maxspeed', 'service', 'access', 'area',
                    'landuse', 'width', 'est_width', 'junction', 'traffic_signals']
ox.utils.config(useful_tags_path)

# define the colors to use for different edge types
hwy_colors = {
        'motorway': 'purple',
        'trunk': 'pink',
        'primary': 'green',
        'secondary': 'yellow',
        'tertiary': 'orange',
        'unclassified': 'blue',
        'residential': 'red',
        # 'cycleway': 'skyblue',
        # 'service': 'sienna',
        # 'living street': 'lightgreen',
        # 'pedestrian': 'lightskyblue',
    }


# return edge IDs that do not match passed list of hwys
def find_edges(G, hwys):
    edges = []
    for u, v, k, data in G.edges(keys=True, data='highway'):
        check1 = isinstance(data, str) and data not in hwys
        check2 = isinstance(data, list) and all([d not in hwys for d in data])
        if check1 or check2:
            edges.append((u, v, k))
    return set(edges)


In [ ]:
# you can get networks anywhere in the world
#address = "Mayfair, London, England, UK"
#address = 'Doha, Qatar'
#address = 'Manhattan, new york'
#address = 'Los Angeles, California'
address = '30 Aldwych, London WC2B 4BG'
G = ox.graph_from_address(address, network_type="drive", dist=2000)
#G = ox.graph_from_address(address, network_type="drive", dist=2000) #400 edges, 1300 roads
#G = ox.graph_from_address(address, network_type="drive", dist=3000) #8k ..., 2.8k ...

#G = ox.graph_from_address(address, network_type="drive")

#G = ox.graph_from_place("Qatar", network_type="drive")



In [ ]:
nodes, edges = ox.graph_to_gdfs(G)

In [36]:
edges[edges['length'] == np.nan]

Empty GeoDataFrame
Columns: [osmid, name, highway, maxspeed, access, reversed, length, oneway, geometry, lanes, ref, tunnel, junction, bridge, width, est_width, service]
Index: []

In [40]:
#Geo.loc[Geo.highway == 'traffic_signals']
edges['maxspeed'].value_counts()

20 mph              3710
30 mph               187
[20 mph, 30 mph]      11
5 mph                  6
10 mph                 2
Name: maxspeed, dtype: int64

In [44]:
type(edges['length'].iloc[0])

numpy.float64

In [ ]:
# G2 = ox.add_edge_speeds(G)
# G2 = ox.add_edge_travel_times(G2)
# #G2 = ox.add_node_elevations() Needs google API

# #list(G2.edges())
# #list(G2.edges(data=True)) To get edges data

# nodes, edges = ox.graph_to_gdfs(G2) #retursn a geodataFrame (nodes and edges data (just like a pandas dataframe))



In [ ]:
print(len(edges))
print(len(edges['name'].value_counts()))

In [ ]:
# #nodes.loc[nodes.index == 21651906]
# nodes
# #nodes.loc[nodes.highway == 'traffic_signals']
# edges


# #GeoGraph = ox.graph_from_gdfs(Geo, edges)
# ox.plot_graph_folium(G2)

# nodes

In [ ]:
# #print(len(nodes), len(Geo))

# len(nodes.loc[nodes.highway == 'traffic_signals'])

# # print(nodes['highway'].value_counts())

# # print(Geo['highway'].value_counts())

# # Geo
# #Geo
# list(edges.iloc[0].geometry.coords)
# #edges.iloc[0]

In [ ]:
#pd.merge(nodes, Geo, on=['geometry'], how='inner')

In [ ]:
edges.name = (edges.name).astype(str)

In [ ]:
names = edges.name.unique()

In [ ]:
notFoundCounter = 0
for name in names:
    if edges.loc[edges['name'] == name]['lanes'].isnull().all():
        notFoundCounter += 1

In [ ]:
print('percentage  of road missing number of lanes = ', notFoundCounter / len(names) * 100)

In [ ]:
print('percentage of edges missing number of lanes = ', edges['lanes'].isnull().sum() / len(edges) * 100)

In [ ]:
notFoundCounter = 0
for name in names:
    if edges.loc[edges['name'] == name]['oneway'].isnull().all():
        notFoundCounter += 1

In [ ]:
print('percentage  of road missing number of lanes = ', notFoundCounter / len(names) * 100)

In [ ]:
edges.loc[edges['name'] == 'Hallam Street']['lanes'].isnull().all()

In [ ]:
edges.loc[edges['name'] == 'Hallam Street']['oneway']#.isnull().all()

In [ ]:
edges.lanes.value_counts()

In [ ]:
edges

In [ ]:
# m = ox.plot_graph_folium(G2) #Interactive map
# m

# first plot all edges that do not appear in hwy_colors's types
# G_tmp = G2.copy()
# G_tmp.remove_edges_from(G.edges - find_edges(G, hwy_colors.keys()))
# if len(G_tmp.edges):
#     m = ox.plot_graph_folium(G_tmp, popup_attribute='highway', weight=5, color='black')
#m = folium.Map()
m = ox.plot_graph_folium(G)
# then plot each edge type in hwy_colors one at a time
for hwy, color in hwy_colors.items():
    G_tmp = G.copy()
    G_tmp.remove_edges_from(find_edges(G_tmp, [hwy]))
    if G_tmp.edges:
        m = ox.plot_graph_folium(G_tmp,
                                 graph_map=m,
                                 popup_attribute='length',
                                 weight=5,
                                 color=color)
        
m


In [29]:
# m = ox.plot_graph_folium(G2) #Interactive map
# m

# first plot all edges that do not appear in hwy_colors's types
# G_tmp = G2.copy()
# G_tmp.remove_edges_from(G.edges - find_edges(G, hwy_colors.keys()))
# if len(G_tmp.edges):
#     m = ox.plot_graph_folium(G_tmp, popup_attribute='highway', weight=5, color='black')
#m = folium.Map()
m = ox.plot_graph_folium(G)
# then plot each edge type in hwy_colors one at a time
for hwy, color in hwy_colors.items():
    G_tmp = G.copy()
    G_tmp.remove_edges_from(find_edges(G_tmp, [hwy]))
    if G_tmp.edges:
        m = ox.plot_graph_folium(G_tmp,
                                 graph_map=m,
                                 popup_attribute='maxspeed',
                                 weight=5,
                                 color=color)
        
m


In [ ]:
fig, ax = ox.plot_graph(G)

In [ ]:
fig, ax = ox.plot_graph(G, node_size=0, edge_linewidth=0.1)